In [1]:
import pandas as pd
from sodapy import Socrata
import datetime as dt
import calendar

In [2]:
import plotly.express as px
import plotly.graph_objects as go
import chart_studio.plotly as py
import plotly.offline as po

In [3]:
def re_idx_name(data, ogcol, rename=None):
    """
    Funcion que re-organiza las columnas en un Dataframe

    Parametros
    ----------
    :param data: Dataframe
    :param ogcol: Orden de las columnas con sus nombres originales
    :param rename: Si se quiere renombrar alguna columna,
    se le pasa un Dict que contenga el nombre de la columna original
    y su nuevo nombre. De la forma {'nombre': 'Nombre'}

    Return
    ----------
    :return: Dataframe reindexado
    """
    try:
        data = data.reindex(ogcol, axis=1)
        if rename:
            data.rename(columns=rename, inplace=True)
            return data
        return data
    except TypeError:
        print('TypeError: Insert a dict in rename place')
    except Exception as e:
        return e

In [4]:
po.init_notebook_mode(connected = True)

In [5]:
df = pd.read_csv('./COVID-19_Reported_Patient_Impact_and_Hospital_Capacity_by_State_Timeseries.csv')

In [6]:
df.drop_duplicates(inplace=True)
df.fillna(0, inplace=True)

In [7]:
df2 = df.drop(df.iloc[:, 98:], axis=1)
df2.drop(columns=['previous_day_admission_adult_covid_confirmed', 'previous_day_admission_pediatric_covid_confirmed'], inplace=True)
df2.drop(df2.filter(regex='coverage|numerator|denominator|suspected|reported|utilization|unknown|percent|geo').columns, axis=1, inplace=True)

In [8]:
us_state_to_abbrev = {
    "Alabama": "AL",
    "Alaska": "AK",
    "Arizona": "AZ",
    "Arkansas": "AR",
    "California": "CA",
    "Colorado": "CO",
    "Connecticut": "CT",
    "Delaware": "DE",
    "Florida": "FL",
    "Georgia": "GA",
    "Hawaii": "HI",
    "Idaho": "ID",
    "Illinois": "IL",
    "Indiana": "IN",
    "Iowa": "IA",
    "Kansas": "KS",
    "Kentucky": "KY",
    "Louisiana": "LA",
    "Maine": "ME",
    "Maryland": "MD",
    "Massachusetts": "MA",
    "Michigan": "MI",
    "Minnesota": "MN",
    "Mississippi": "MS",
    "Missouri": "MO",
    "Montana": "MT",
    "Nebraska": "NE",
    "Nevada": "NV",
    "New Hampshire": "NH",
    "New Jersey": "NJ",
    "New Mexico": "NM",
    "New York": "NY",
    "North Carolina": "NC",
    "North Dakota": "ND",
    "Ohio": "OH",
    "Oklahoma": "OK",
    "Oregon": "OR",
    "Pennsylvania": "PA",
    "Rhode Island": "RI",
    "South Carolina": "SC",
    "South Dakota": "SD",
    "Tennessee": "TN",
    "Texas": "TX",
    "Utah": "UT",
    "Vermont": "VT",
    "Virginia": "VA",
    "Washington": "WA",
    "West Virginia": "WV",
    "Wisconsin": "WI",
    "Wyoming": "WY",
    "District of Columbia": "DC",
    "American Samoa": "AS",
    "Guam": "GU",
    "Northern Mariana Islands": "MP",
    "Puerto Rico": "PR",
    "United States Minor Outlying Islands": "UM",
    "U.S. Virgin Islands": "VI",
}
    
# invert the dictionary
abbrev_to_us_state = dict(map(reversed, us_state_to_abbrev.items()))

In [9]:
df2['date'] = pd.to_datetime(df2['date'])
df2['month'] = df2['date'].dt.month
df2['total_hospitalized'] = df2['total_adult_patients_hospitalized_confirmed_covid'] + df2['total_pediatric_patients_hospitalized_confirmed_covid']
df2['state_name'] = df2['state'].replace(abbrev_to_us_state)
df2 = df2.convert_dtypes()
df2.reset_index(drop=True, inplace=True)

In [10]:
s5m = df2.loc[df2['date'].dt.year == 2020]
s5m = s5m.groupby('state').apply(lambda x: x[x['month'] <= 6][['inpatient_beds_used_covid', 'total_adult_patients_hospitalized_confirmed_covid', 'deaths_covid']].sum())

# 1.

In [11]:
s5m = s5m.loc[s5m['inpatient_beds_used_covid'].nlargest(5).index]
dat_col = list(s5m.columns)
s5m = re_idx_name(s5m, dat_col, {'inpatient_beds_used_covid': 'Camas UCI COVID',
 'total_adult_patients_hospitalized_confirmed_covid': 'Adultos Hospitalizados',
 'deaths_covid': 'Muertes'})

In [12]:
s5m

Camas UCI COVID  Adultos Hospitalizados  Muertes
state                                                  
NY              686528                      87    50099
CA              434721                   36134     9446
FL              322227                       0     2319
TX              246237                       0     2264
IL              214010                       0     3729

# 2.

In [13]:
new_york = df2.sort_values(by='date')
new_york = new_york.loc[(new_york['date'] >= '2020-03-20') & (new_york['date'] <= '2021-06-15') & (new_york['state'] == 'NY')]
new_york.reset_index(drop=True, inplace=True)

In [14]:
nyfig = px.line(new_york, x='date', y=['inpatient_beds_used_covid', 'deaths_covid'])
nyfig.update_layout(title='Ocupacion de Camas New York', xaxis_title='Año',
                yaxis_title='Camas Usadas', hovermode='x unified')
var = {'inpatient_beds_used_covid': 'Camas Covid', 'deaths_covid': 'Muertes Covid'}
nyfig.for_each_trace(lambda t: t.update(name = var[t.name], legendgroup = var[t.name],
                    hovertemplate = t.hovertemplate.replace(t.name, var[t.name])))
nyfig.update_layout(xaxis=dict(showgrid=False),
              yaxis=dict(showgrid=False))

# 3.

In [15]:
most_beds = df2.groupby('state').apply(lambda x: x[x['date'].dt.year == 2020][['inpatient_beds', 'inpatient_beds_used', 'inpatient_beds_used_covid']].sum())
most_beds = most_beds.loc[most_beds['inpatient_beds_used'].nlargest(5).index]
most_beds.reset_index(inplace=True); most_beds
dat_col2 = list(most_beds.columns)
most_beds = re_idx_name(most_beds, dat_col2, {'state': 'Estado',
'inpatient_beds': 'Camas UCI Disponibles',
'inpatient_beds_used': 'Camas UCI Normal',
'inpatient_beds_used_covid': 'Camas UCI COVID'})

In [16]:
bedsfig = px.histogram(most_beds, y='Camas UCI Normal', x='Estado', text_auto=True, color='Estado', 
                color_discrete_sequence = px.colors.sequential.PuRd_r)
bedsfig.update_layout(title='Ocupacion de Camas UCI por estado', xaxis_title='Estado',
                yaxis_title='Camas UCI Utilizadas')

# 4.

In [17]:
kids_bed = df2.groupby('state').apply(lambda x: x[x['date'].dt.year == 2020][['total_pediatric_patients_hospitalized_confirmed_covid']].sum())
kids_bed.reset_index(inplace=True)
kids_bed.sort_values(by='total_pediatric_patients_hospitalized_confirmed_covid', ascending=False, inplace=True)

In [18]:
kfig = px.histogram(kids_bed, y='total_pediatric_patients_hospitalized_confirmed_covid', x='state', 
                color_discrete_sequence = px.colors.diverging.Geyser)
kfig.update_layout(title='Camas pediatricas UCI por estado', xaxis_title='Estado',
                yaxis_title='Camas UCI Utilizadas')
kfig.update_xaxes(tickangle=325)
kfig.update_layout(xaxis=dict(showgrid=False),
              yaxis=dict(showgrid=False))

# 5.

In [19]:
uci_beds = df2.groupby('state')[['inpatient_beds', 'inpatient_beds_used_covid']].sum()
uci_beds['usage_percent'] = round((uci_beds['inpatient_beds_used_covid'] / uci_beds['inpatient_beds']) * 100, 2)
uci_beds.sort_values(by='usage_percent', ascending=False, inplace=True)

In [20]:
uci_plot = uci_beds.copy()
uci_plot.reset_index(inplace=True)

In [21]:
uci_b = go.Figure()
uci_b.add_trace(go.Bar(x=uci_plot.state, y=uci_plot.inpatient_beds, name='Camas UCI Totales', marker_color='indianred'))
uci_b.add_trace(go.Bar(x=uci_plot.state, y=uci_plot.inpatient_beds_used_covid, 
                    name='Camas UCI COVID', marker_color='lightsalmon'))

uci_b.update_layout(barmode='group', xaxis_tickangle=-45,
                    xaxis=dict(showgrid=False),
                    yaxis=dict(showgrid=False))
uci_b.show()

# 6.

In [22]:
deaths = df2.groupby('state').apply(lambda x: x[x['date'].dt.year == 2021][['deaths_covid']].sum())
deaths.reset_index(inplace=True)
deaths.sort_values(by='deaths_covid', inplace=True)

In [23]:
death = px.bar(deaths, x='state', y='deaths_covid', color_discrete_sequence = px.colors.diverging.Spectral)
death.update_layout(title='Muertes COVID por estado 2021', xaxis_title='Estado',
                yaxis_title='Muertes')
death.update_xaxes(tickangle=-45)
death.update_layout(xaxis=dict(showgrid=False),
              yaxis=dict(showgrid=False))
death.show()

# 7.

In [24]:
staff = df2.groupby('state').apply(lambda x: x[x['date'].dt.year == 2021][['critical_staffing_shortage_today_yes', 'deaths_covid']].sum())
staff2 = staff.copy()
staff2.reset_index(inplace=True)

In [25]:
sf = px.histogram(staff2, x='state', y=['critical_staffing_shortage_today_yes', 'deaths_covid'])
sf.update_layout(title='Muertes x Falta de Equipo 2021', xaxis_title='Estado',
                yaxis_title='Muertes/Equipo', xaxis=dict(showgrid=False),
              yaxis=dict(showgrid=False), hovermode='x unified')
var2 = {'critical_staffing_shortage_today_yes': 'Camas Faltantes', 'deaths_covid': 'Muertes Covid'}
sf.for_each_trace(lambda t: t.update(name = var2[t.name], legendgroup = var2[t.name],
                    hovertemplate = t.hovertemplate.replace(t.name, var2[t.name])))
sf.update_xaxes(tickangle=-45)

sf.show()

# 8.

In [26]:
worst_year = df2.groupby([df2.date.dt.year, df2.date.dt.month])[['deaths_covid', 'critical_staffing_shortage_today_yes']].sum()
worst_year.reset_index(level=1, inplace=True)
worst_year.rename(columns={'date': 'month'}, inplace=True)
worst_year = worst_year.rename_axis('year', axis='index')
worst_month = worst_year.copy()
worst_month = worst_month.groupby('month').sum()
worst_month.rename(index=lambda x: calendar.month_abbr[x], inplace=True)

In [27]:
monthfig = go.Figure()
monthfig.add_trace(go.Bar(x=worst_month.index.values, y=worst_month.deaths_covid, name='Muertes', marker_color='crimson'))
monthfig.add_trace(go.Bar(x=worst_month.index.values, y=worst_month.critical_staffing_shortage_today_yes, name='Equipo Faltante', marker_color='coral'))
monthfig.update_layout(title='Muertes x Mes (Toda la pandemia)', xaxis_title='Mes',
                yaxis_title='Muertes / Falta Equipo', barmode='group',
                    xaxis=dict(showgrid=False),
                    yaxis=dict(showgrid=False), hovermode='x unified')
monthfig.show()

# *DASHBOARD*

In [36]:
hospt = df2.groupby('state')[['total_hospitalized']].sum()
hospt.reset_index(inplace=True)
hospt['state_name'] = hospt['state'].replace(abbrev_to_us_state)
hospt.sort_values(by='total_hospitalized', ascending=False, inplace=True)
hospt.drop(columns='state', inplace=True)
dat_col3 = ['total_hospitalized', 'state_name']
hospt = re_idx_name(hospt, dat_col3, {'state_name': 'Estado', 'total_hospitalized': 'Hospitalizados_COVID'})
hospt.reset_index(drop=True, inplace=True)

In [29]:
hospt

Hospitalizados COVID                Estado
0                4144374                 Texas
1                4039850            California
2                3351715               Florida
3                2306009              New York
4                1641943          Pennsylvania
5                1497300               Georgia
6                1477493                  Ohio
7                1333997              Illinois
8                1207124              Michigan
9                1154069        North Carolina
10               1007121            New Jersey
11                997211               Arizona
12                984435             Tennessee
13                900083              Missouri
14                837165               Indiana
15                783056              Virginia
16                780244               Alabama
17                733839             Louisiana
18                635039              Kentucky
19                619740        South Carolina
20                591941              Maryland
21                586524             Wisconsin
22                558945                Nevada
23                555291              Oklahoma
24                527807            Washington
25                481650         Massachusetts
26                480928             Minnesota
27                474501              Colorado
28                411127              Arkansas
29                408485           Mississippi
30                321968           Connecticut
31                312551                Kansas
32                309085         West Virginia
33                295043                  Iowa
34                293275                Oregon
35                235988            New Mexico
36                226727                  Utah
37                222855              Nebraska
38                184423                 Idaho
39                176268           Puerto Rico
40                132700              Delaware
41                123767               Montana
42                114866  District of Columbia
43                109098                 Maine
44                108285          Rhode Island
45                108074          South Dakota
46                 98186          North Dakota
47                 92496         New Hampshire
48                 90902                Hawaii
49                 56964               Wyoming
50                 55629                Alaska
51                 24219               Vermont
52                  5002   U.S. Virgin Islands
53                   736        American Samoa

In [39]:
usa_map = px.choropleth_mapbox(hospt, 
                geojson='https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json', 
                locations='Estado', featureidkey='properties.name',
                color='Hospitalizados_COVID', color_continuous_scale='Reds', 
                mapbox_style="carto-positron", zoom=3, center = {"lat": 37.0902, "lon": -95.7129},
                opacity=0.5, labels={'Hospitalizados_COVID':'Total Hospitalizados'})
usa_map.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
usa_map.show()

In [30]:
eeuu_map = df2.copy()
eeuu_map['date'] = eeuu_map['date'].dt.strftime('%Y-%m-%d')
eeuu_map.sort_values(by='date', inplace=True)

In [31]:

usa_map2 = px.choropleth_mapbox(eeuu_map, 
                geojson='https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json', 
                locations='state_name', featureidkey='properties.name',
                color='total_hospitalized', color_continuous_scale='Reds', 
                mapbox_style="carto-positron", zoom=3, center = {"lat": 37.0902, "lon": -95.7129},
                opacity=0.5, labels={'total_hospitalized':'Total Hospitalizados',
                 'state_name': 'Estado',
                 'date': 'Fecha'}, animation_frame='date')
usa_map2.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
usa_map2.show()

In [32]:
bed_timeline = df2.copy()
bed_timeline['date'] = bed_timeline['date'].dt.strftime('%Y-%m-%d')
bed_timeline.sort_values(by='date', inplace=True)

In [33]:
timelinefig = px.choropleth_mapbox(bed_timeline, 
                geojson='https://raw.githubusercontent.com/PublicaMundi/MappingAPI/master/data/geojson/us-states.json', 
                locations='state_name', featureidkey='properties.name',
                color='inpatient_beds_used_covid', color_continuous_scale='Inferno_r', 
                mapbox_style="carto-positron", zoom=3, center = {"lat": 37.0902, "lon": -95.7129},
                opacity=0.5, labels={'inpatient_beds_used_covid':'Total Camas',
                 'state_name': 'Estado',
                 'date': 'Fecha'}, animation_frame='date')
timelinefig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
